In [1]:
from glob import glob
import os

from IPython.display import Image

from sourmash_lib import signature
from sbt import SBT, GraphFactory, SigLeaf, Node
from sbtmh import search_minhashes

In [2]:
%%timeit
factory = GraphFactory(31, 1e5, 4)
tree = SBT(factory)
for f in glob("urchin/*.sig"):
    with open(f, 'r') as data:
        sig = signature.load_signatures(data)
    leaf = SigLeaf(os.path.basename(f), sig[0])
    tree.add_node(leaf)
    to_search = leaf

1 loop, best of 3: 11 s per loop


In [3]:
factory = GraphFactory(31, 1e5, 4)
tree = SBT(factory)
for f in glob("urchin/*.sig"):
    with open(f, 'r') as data:
        sig = signature.load_signatures(data)
    leaf = SigLeaf(os.path.basename(f), sig[0])
    tree.add_node(leaf)
    to_search = leaf
tree.print()

 *Node:internal.0 [occupied: 40740, fpr: 0.028]
     *Node:internal.2 [occupied: 23753, fpr: 0.0032]
         *Node:internal.6 [occupied: 13412, fpr: 0.00032]
             *Node:internal.14 [occupied: 6986, fpr: 2.4e-05]
                 *Node:internal.30 [occupied: 3888, fpr: 2.3e-06]
                     *Node:internal.62 [occupied: 1950, fpr: 1.4e-07]
                         *Node:internal.126 [occupied: 987, fpr: 9.5e-09]
                             **Leaf:californicus-SRR1695477.sig -> californicus-SRR1695477.sig
                             **Leaf:longicauda-SRR1325051.sig -> longicauda-SRR1325051.sig
                         *Node:internal.125 [occupied: 990, fpr: 9.6e-09]
                             **Leaf:rubens-SRR1139190.sig -> rubens-SRR1139190.sig
                             **Leaf:agassizii-SRR1695485.sig -> agassizii-SRR1695485.sig
                     *Node:internal.61 [occupied: 1972, fpr: 1.5e-07]
                         *Node:internal.124 [occupied: 992, fpr: 9.

In [4]:
len(tree.nodes)

511

In [5]:
%%capture dag
tree.print_dot()

In [6]:
with open('dag.dot', 'w') as f:
    f.write(dag.stdout)
!twopi -Tpng -Granksep="5 equally" -Nshape=ellipse dag.dot > tree.png
Image("tree.png")

In [7]:
%%timeit
tree.find(search_minhashes, to_search.data, 0.1)

100 loops, best of 3: 11.6 ms per loop


In [8]:
print('*' * 60)
print("{}:".format(to_search.metadata))
print(*[(str(s.metadata), s.data.similarity(to_search.data)) for s in tree.find(search_minhashes, to_search.data, 0.1)],
      sep='\n')

************************************************************
lividus-SRR1735497.sig:
('lividus-SRR1735501.sig', 0.3619999885559082)
('lividus-SRR1664663.sig', 0.41600000858306885)
('lividus-SRR1735498.sig', 0.47999998927116394)
('lividus-SRR1735500.sig', 0.4059999883174896)
('lividus-SRR1735496.sig', 0.421999990940094)
('lividus-SRR1735499.sig', 0.4580000042915344)
('lividus-SRR1735497.sig', 1.0)
